In [41]:
import ast
import csv
import json

import numpy as np
import pandas as pd

import matplotlib.pyplot as plt
from matplotlib_venn import venn2, venn2_circles

import plotly
from plotly.offline import iplot, init_notebook_mode
import plotly.graph_objs as go
import plotly.express as px

pd.set_option('display.max_columns', None)

In [46]:
df_09 = pd.read_csv('../data/interim/ds_dedup09.csv', sep=';')
df_09.head(10)

dedup_id  \
0  dedup::29a83a8a9641bb860a679d7e5ba52d26   
1  dedup::000871c1fc726f0b52dc86a4eeb027de   
2  dedup::000871c1fc726f0b52dc86a4eeb027de   
3  dedup::001e6d882e54c780ce269d3c46997287   
4  dedup::001e6d882e54c780ce269d3c46997287   
5  dedup::0023a1e3447fdb31836536cc903f1310   
6  dedup::0023a1e3447fdb31836536cc903f1310   
7  dedup::003ab6b40af9b488decea7c582d150a2   
8  dedup::003ab6b40af9b488decea7c582d150a2   
9  dedup::0064f599ed0adb5870a5b3ffe438e485   

                                        duplicate_id  \
0                                              14174   
1                                               4612   
2                                               4649   
3     re3data_____::4af9fe2bb93511a5e0f0c39e94d6557f   
4  https://fairsharing.org/10.25504/FAIRsharing.q...   
5     opendoar____::c6f798b844366ccd65d99bc7f31e0e02   
6                                              10013   
7  https://fairsharing.org/10.25504/FAIRsharing.d...   
8     re3data_____::cafc5d99b7c187e24b40d958a16a91f1   
9                                              16034   

                                         original_id  \
0                                              14174   
1                                               4612   
2                                               4649   
3                                       r3d100011306   
4  https://fairsharing.org/10.25504/FAIRsharing.q...   
5                                               3410   
6                                              10013   
7  https://fairsharing.org/10.25504/FAIRsharing.d...   
8                                       r3d100011894   
9                                              16034   

                                                name       source  
0       OHIO Open Library | Ohio University Research         roar  
1                IIT Bombay Institutional Repository         roar  
2                IIT Bombay Institutional Repository         roar  
3            RESID Database of Protein Modifications      re3data  
4            RESID Database of Protein Modifications  FAIRsharing  
5  erucu: electronic repository of the ukrainian ...     OpenDOAR  
6  ErUCU: Electronic repository of the Ukrainian ...         roar  
7                                            Synapse  FAIRsharing  
8                                            Synapse      re3data  
9        Giresun University Institutional Repository         roar

In [24]:
df_09[df_09.dedup_id == 'dedup::ffeed84c7cb1ae7bf4ec4bd78275bb98']

dedup_id  \
5115  dedup::ffeed84c7cb1ae7bf4ec4bd78275bb98   
5116  dedup::ffeed84c7cb1ae7bf4ec4bd78275bb98   

                                        duplicate_id original_id  \
5115                                            1126        1126   
5116  opendoar____::443cb001c138b2561a0d90720d6ce111         648   

                           name    source  
5115  RIT Digital Media Library      roar  
5116  rit digital media library  OpenDOAR

In [25]:
df_09[df_09.dedup_id == 'dedup::01846ae470651e97d2f73fce979406a9']

dedup_id  \
40  dedup::01846ae470651e97d2f73fce979406a9   

                                      duplicate_id original_id  \
40  opendoar____::b4d6f2b565ca0eef1f9245403aac366a        7668   

                                                 name    source  
40  digital commons at michigan state university c...  OpenDOAR

In [3]:
re3data_df = pd.read_csv('../data/raw/re3data.tsv', delimiter='\t', 
                        converters={'subject': ast.literal_eval,
                                    'keyword': ast.literal_eval,
                                    'additional_name': ast.literal_eval,
                                    'repository_id': ast.literal_eval,
                                    'type': ast.literal_eval,
                                    'content_type': ast.literal_eval,
                                    'provider_type': ast.literal_eval,
                                    'institution': ast.literal_eval
                                    })

In [4]:
opendoar_df = pd.read_csv('../data/raw/openDoar.tsv', delimiter='\t',
                         converters={'subject': ast.literal_eval,
                                    'additional_name': ast.literal_eval,
                                    'opendoar_id': ast.literal_eval,
                                    'content_type': ast.literal_eval,
                                    'institution': ast.literal_eval
                                    })

In [5]:
roar_df = pd.read_csv('../data/raw/export_roar_CSV.csv', dtype='str')

In [6]:
fairsharing_df = pd.read_csv('../data/raw/FAIRsharingDBrec_summary20210304.csv', 
                             delimiter='|', header=0,
                             names=['full_name', 'short_name', 'fs_url', 'url', 'countries', 'subjects'])

In [7]:
df_09.head()

dedup_id  \
0  dedup::29a83a8a9641bb860a679d7e5ba52d26   
1  dedup::000871c1fc726f0b52dc86a4eeb027de   
2  dedup::000871c1fc726f0b52dc86a4eeb027de   
3  dedup::001e6d882e54c780ce269d3c46997287   
4  dedup::001e6d882e54c780ce269d3c46997287   

                                        duplicate_id  \
0                                              14174   
1                                               4612   
2                                               4649   
3     re3data_____::4af9fe2bb93511a5e0f0c39e94d6557f   
4  https://fairsharing.org/10.25504/FAIRsharing.q...   

                                         original_id  \
0                                              14174   
1                                               4612   
2                                               4649   
3                                       r3d100011306   
4  https://fairsharing.org/10.25504/FAIRsharing.q...   

                                           name       source  
0  OHIO Open Library | Ohio University Research         roar  
1           IIT Bombay Institutional Repository         roar  
2           IIT Bombay Institutional Repository         roar  
3       RESID Database of Protein Modifications      re3data  
4       RESID Database of Protein Modifications  FAIRsharing

In [8]:
dup = df_09.groupby('dedup_id').aggregate(list)
dup

duplicate_id  \
dedup_id                                                                                     
dedup::000871c1fc726f0b52dc86a4eeb027de                                       [4612, 4649]   
dedup::001e6d882e54c780ce269d3c46997287  [re3data_____::4af9fe2bb93511a5e0f0c39e94d6557...   
dedup::0023a1e3447fdb31836536cc903f1310  [opendoar____::c6f798b844366ccd65d99bc7f31e0e0...   
dedup::003ab6b40af9b488decea7c582d150a2  [https://fairsharing.org/10.25504/FAIRsharing....   
dedup::0064f599ed0adb5870a5b3ffe438e485  [16034, opendoar____::d1f157379ea7e51d4a8c07af...   
...                                                                                    ...   
dedup::ff49cc40a8890e6a60f40ff3026d2730  [1333, opendoar____::2bd7f907b7f5b6bbd91822c0c...   
dedup::ff4d70de478038c72282b7e4af1d4260  [opendoar____::95a0810a93a87065bf7b28490817e9e...   
dedup::ff826ce6ee85809389f18a5fafe72366  [opendoar____::62e7f2e090fe150ef8deb4466fdc81b...   
dedup::ffbd6cbb019a1413183c8d08f2929307  [3108, opendoar____::ff7d0f525b3be596a51fb9194...   
dedup::ffeed84c7cb1ae7bf4ec4bd78275bb98  [1126, opendoar____::443cb001c138b2561a0d90720...   

                                                                               original_id  \
dedup_id                                                                                     
dedup::000871c1fc726f0b52dc86a4eeb027de                                       [4612, 4649]   
dedup::001e6d882e54c780ce269d3c46997287  [r3d100011306, https://fairsharing.org/10.2550...   
dedup::0023a1e3447fdb31836536cc903f1310                                      [3410, 10013]   
dedup::003ab6b40af9b488decea7c582d150a2  [https://fairsharing.org/10.25504/FAIRsharing....   
dedup::0064f599ed0adb5870a5b3ffe438e485                                      [16034, 9647]   
...                                                                                    ...   
dedup::ff49cc40a8890e6a60f40ff3026d2730                                       [1333, 1389]   
dedup::ff4d70de478038c72282b7e4af1d4260                                      [9752, 16367]   
dedup::ff826ce6ee85809389f18a5fafe72366                                       [3601, 2608]   
dedup::ffbd6cbb019a1413183c8d08f2929307                                       [3108, 1912]   
dedup::ffeed84c7cb1ae7bf4ec4bd78275bb98                                        [1126, 648]   

                                                                                      name  \
dedup_id                                                                                     
dedup::000871c1fc726f0b52dc86a4eeb027de  [IIT Bombay Institutional Repository, IIT Bomb...   
dedup::001e6d882e54c780ce269d3c46997287  [RESID Database of Protein Modifications, RESI...   
dedup::0023a1e3447fdb31836536cc903f1310  [erucu: electronic repository of the ukrainian...   
dedup::003ab6b40af9b488decea7c582d150a2                                 [Synapse, Synapse]   
dedup::0064f599ed0adb5870a5b3ffe438e485  [Giresun University Institutional Repository, ...   
...                                                                                    ...   
dedup::ff49cc40a8890e6a60f40ff3026d2730                     [UnissResearch, unissresearch]   
dedup::ff4d70de478038c72282b7e4af1d4260  [european xfel publication database, European ...   
dedup::ff826ce6ee85809389f18a5fafe72366  [electronic odessa national economic universit...   
dedup::ffbd6cbb019a1413183c8d08f2929307  [Fotografía Sobre España en el Siglo XIX, foto...   
dedup::ffeed84c7cb1ae7bf4ec4bd78275bb98  [RIT Digital Media Library, rit digital media ...   

                                                         source  
dedup_id                                                         
dedup::000871c1fc726f0b52dc86a4eeb027de            [roar, roar]  
dedup::001e6d882e54c780ce269d3c46997287  [re3data, FAIRsharing]  
dedup::0023a1e3447fdb31836536cc903f1310        [OpenDOAR, roar]  
dedup::003ab6b40af9b488decea7c582d150a2  [FAIRsharing, re3data]  
dedup::0064f5

In [9]:
dup[dup.source.str.len() == 1]

duplicate_id  \
dedup_id                                                                                     
dedup::01846ae470651e97d2f73fce979406a9   [opendoar____::b4d6f2b565ca0eef1f9245403aac366a]   
dedup::022036087426786cfd0f7f41fa7a2665  [https://fairsharing.org/10.25504/FAIRsharing....   
dedup::07e8b472e1e4af17a6b20ce083baf29f                                            [15036]   
dedup::0894634a3244e3050d8057a453e17e57  [https://fairsharing.org/10.25504/FAIRsharing....   
dedup::0a54b19a13b6712dc04d1b49215423d8   [opendoar____::d34ab169b70c9dcd35e62896010cd9ff]   
...                                                                                    ...   
dedup::f8306c8f16096b6d944799f4d427a976   [re3data_____::574b553c6c374d597d2068ab2b117889]   
dedup::f9d8e2daaa9144310b66bf948e50d656   [re3data_____::95014789f83d7611ebfddace19d0523a]   
dedup::fcdbc4f504a15df8f78da88ee72fad32   [opendoar____::9f96f36b7aae3b1ff847c26ac94c604e]   
dedup::fcfe9c770eb9372e6961a17f7eaffd5f                                             [4637]   
dedup::fe73f687e5bc5280214e0486b273a5f9                                              [330]   

                                                                               original_id  \
dedup_id                                                                                     
dedup::01846ae470651e97d2f73fce979406a9                                             [7668]   
dedup::022036087426786cfd0f7f41fa7a2665  [https://fairsharing.org/10.25504/FAIRsharing....   
dedup::07e8b472e1e4af17a6b20ce083baf29f                                            [15036]   
dedup::0894634a3244e3050d8057a453e17e57  [https://fairsharing.org/10.25504/FAIRsharing....   
dedup::0a54b19a13b6712dc04d1b49215423d8                                              [377]   
...                                                                                    ...   
dedup::f8306c8f16096b6d944799f4d427a976                                     [r3d100012041]   
dedup::f9d8e2daaa9144310b66bf948e50d656                                     [r3d100011045]   
dedup::fcdbc4f504a15df8f78da88ee72fad32                                             [4979]   
dedup::fcfe9c770eb9372e6961a17f7eaffd5f                                             [4637]   
dedup::fe73f687e5bc5280214e0486b273a5f9                                              [330]   

                                                                                      name  \
dedup_id                                                                                     
dedup::01846ae470651e97d2f73fce979406a9  [digital commons at michigan state university ...   
dedup::022036087426786cfd0f7f41fa7a2665            [World Data Center for Climate at DRKZ]   
dedup::07e8b472e1e4af17a6b20ce083baf29f                                          [MiCISAN]   
dedup::0894634a3244e3050d8057a453e17e57                       [European Variation Archive]   
dedup::0a54b19a13b6712dc04d1b49215423d8             [yale medicine thesis digital library]   
...                                                                                    ...   
dedup::f8306c8f16096b6d944799f4d427a976                       [Canadian Disaster Database]   
dedup::f9d8e2daaa9144310b66bf948e50d656  [Index to Marine & Lacustrine Geological Samples]   
dedup::fcdbc4f504a15df8f78da88ee72fad32               [university of minnesota law school]   
dedup::fcfe9c770eb9372e6961a17f7eaffd5f  [Simon Fraser University Institutional Reposit...   
dedup::fe73f687e5bc5280214e0486b273a5f9  [DigitalCommons@Fort Lewis College: Scholarshi...   

                                                source  
dedup_id                                                
dedup::01846ae470651e97d2f73fce979406a9     [OpenDOAR]  
dedup::022036087426786cfd0f7f41fa7a2665  [FAIRsharing]  
dedup::07e8b472e1e4af17a6b20ce083baf29f         [roar]  
dedup::0894634a3244e3050d8057a453e17e57  [FAIRsharing]  
dedup::0a54b19a13b6712dc04d1b49215423d8     [OpenDOAR]  
...       

In [10]:
dup[dup.source.str.len() >= 6].original_id.values

array([list(['r3d100013204', 'r3d100013458', 'r3d100012807', 'r3d100012808', 'r3d100012806', 'r3d100012805']),
       list(['243', '5702', '5715', '5694', '5689', '5658', '5710', '5750', '5721', '5704']),
       list(['2738', '4991', '2727', '2729', '2724', '2728', '2740', '174']),
       list(['19', '8', '7', '11', '10', '13', '6', '12', '20', '15', '9', '5', '14', '16'])],
      dtype=object)

In [11]:
pd.DataFrame(re3data_df[re3data_df.re3data_id.isin(['r3d100013204', 'r3d100013458', 'r3d100012807', 'r3d100012808', 'r3d100012806', 'r3d100012805'])].institution.to_list())

0  \
0  [Harvard University, Institute for Quantitativ...   
1  [Dataverse Project, [], AAA, [technical], non-...   
2  [Harvard University, Institute for Quantitativ...   
3  [Harvard University, Institute for Quantitativ...   
4  [University of Victoria, [UVic], CAN, [general...   
5  [The University of British Columbia, [], CAN, ...   

                                                   1  \
0  [Ontario Council of University Libraries, [CBU...   
1  [Harvard University, Institute for Quantitave ...   
2  [Ontario Council of University Libraries, [CBU...   
3  [Ontario Council of University Libraries, [CBU...   
4  [University of Victoria, Libraries, [], CAN, [...   
5  [University of British Columbia, Library, [], ...   

                                                   2  \
0  [Scholars Portal Dataverse, [], CAN, [general]...   
1  [Ontario Council of University Libraries, [CBU...   
2  [Scholars Portal Dataverse, [dataverse@scholar...   
3  [Scholars Portal Dataverse, [], CAN, [general]...   
4                                               None   
5                                               None   

                                                   3  \
0  [The Dataverse Project, [], AAA, [technical], ...   
1  [University of Toronto, Libraries, [], CAN, [g...   
2  [The Dataverse Project, [], AAA, [technical], ...   
3  [The Dataverse Project, [], AAA, [technical], ...   
4                                               None   
5                                               None   

                                                   4  
0  [University of Ottawa, Library, [Université d'...  
1                                               None  
2  [University of Windsor, [], CAN, [general], no...  
3  [University of Waterloo, [], CAN, [general], n...  
4                                               None  
5                                               None

In [12]:
roar_df[roar_df.eprintid.isin(['4612', '4649'])]

eprintid rev_number eprint_status userid importid source  \
4167      4612         28       archive   1380      NaN    NaN   
4168      4612        NaN           NaN    NaN      NaN    NaN   
4169      4612        NaN           NaN    NaN      NaN    NaN   
4170      4612        NaN           NaN    NaN      NaN    NaN   
4171      4612        NaN           NaN    NaN      NaN    NaN   
4172      4612        NaN           NaN    NaN      NaN    NaN   
4173      4612        NaN           NaN    NaN      NaN    NaN   
16436     4649          8       archive   1380      NaN    NaN   
16437     4649        NaN           NaN    NaN      NaN    NaN   

                     dir            datestamp              lastmod  \
4167   disk0/00/00/46/12  2012-01-08 03:17:02  2012-04-16 10:53:04   
4168                 NaN                  NaN                  NaN   
4169                 NaN                  NaN                  NaN   
4170                 NaN                  NaN                  NaN   
4171                 NaN                  NaN                  NaN   
4172                 NaN                  NaN                  NaN   
4173                 NaN                  NaN                  NaN   
16436  disk0/00/00/46/49  2012-02-05 13:57:01  2012-04-16 10:39:58   
16437                NaN                  NaN                  NaN   

            status_changed           type succeeds commentary  \
4167   2012-01-08 03:17:02  institutional      NaN        NaN   
4168                   NaN            NaN      NaN        NaN   
4169                   NaN            NaN      NaN        NaN   
4170                   NaN            NaN      NaN        NaN   
4171                   NaN            NaN      NaN        NaN   
4172                   NaN            NaN      NaN        NaN   
4173                   NaN            NaN      NaN        NaN   
16436  2012-02-05 13:57:01  institutional      NaN        NaN   
16437                  NaN            NaN      NaN        NaN   

      metadata_visibility latitude longitude relation_type relation_uri  \
4167                 show      NaN       NaN           NaN          NaN   
4168                  NaN      NaN       NaN           NaN          NaN   
4169                  NaN      NaN       NaN           NaN          NaN   
4170                  NaN      NaN       NaN           NaN          NaN   
4171                  NaN      NaN       NaN           NaN          NaN   
4172                  NaN      NaN       NaN           NaN          NaN   
4173                  NaN      NaN       NaN           NaN          NaN   
16436                show      NaN       NaN           NaN          NaN   
16437                 NaN      NaN       NaN           NaN          NaN   

      item_issues_id item_issues_type item_issues_description  \
4167             NaN              NaN                     NaN   
4168             NaN              NaN                     NaN   
4169             NaN              NaN                     NaN   
4170             NaN              NaN                     NaN   
4171             NaN              NaN                     NaN   
4172             NaN              NaN                     NaN   
4173             NaN              NaN                     NaN   
16436            NaN              NaN                     NaN   
16437            NaN              NaN                     NaN   

      item_issues_timestamp item_issues_status item_issues_reported_by  \
4167                    NaN                NaN                     NaN   
4168                    NaN                NaN                     NaN   
4169                    NaN                NaN                     NaN   
4170                    NaN                NaN                     NaN   
4171                    NaN                NaN                     NaN   
4172                    NaN                NaN                     NaN   
4173                    NaN                NaN                     NaN   

In [13]:
re3data_df[re3data_df.re3data_id == 'r3d100011306']

openaire_id    re3data_id  \
1090  re3data_____::4af9fe2bb93511a5e0f0c39e94d6557f  r3d100011306   

                              repository_name additional_name  \
1090  RESID Database of Protein Modifications              []   

                                    repository_url  \
1090  https://pir.georgetown.edu/resid/resid.shtml   

                                          repository_id  \
1090  [FAIRsharing_doi:10.25504/FAIRsharing.qaszjp, ...   

                                            description            type size  \
1090  The RESID Database of Protein Modifications is...  [disciplinary]  NaN   

     update_date start_date end_date  \
1090         NaN       2014      NaN   

                                                subject mission_statement  \
1090  [2 Life Sciences, 201 Basic Biological and Med...            false    

                   content_type   provider_type  \
1090  [Images, Structured text]  [dataProvider]   

                                                keyword  \
1090  [genomes, life sciences, proteins, proteomes, ...   

                                            institution policy  \
1090  [[Georgetown University, Medical Center, [GUMC...  true    

     database_access database_license data_access data_license data_upload  \
1090           true            false        true         true        true    

     data_upload_license software versioning    api pid_system  \
1090              false     true         yes  true       true    

     citation_guideline_url aid_system enhanced_publication  \
1090                  true       true                   yes   

     quality_management certificate metadata_standard syndication  \
1090            unknown      false             false       false    

                                                remarks  entry_date  \
1090  RESID is covered by Thomson Reuters Data Citat...  2014-12-05   

     last_update  
1090  2019-01-17